# Project Description

## Motivation


<i><b>For Jan</b>: Insert business value</i>

## Data Source

<i><b>For Jan</b>: Insert write up</i>

Note: https://www.sciencedirect.com/science/article/abs/pii/S0379073824001944

## Main Problem

<i><b>For Jan</b>: Insert main problem</i>

Sample: What models can be recommended that provides the highest accuracy depending on the resolution level?

## Limitations

In the study "YHP: Y-chromosome Haplogroup Predictor for predicting male lineages based on Y-STRs", the researchers classified the different haplogroups into 18 resolutions, wherein each resolution was used to train and test the different machine learning models. Grouping the haplogroups into resolutions requires further research to ensure correctness of classification. 

With this in mind, this study no longer classified the haplogroups into resolution. Instead, the entire data set was utilized in training and testing machine learning models.

# Methodology

Step 1. Identify the Business Problem

Step 2. Identify the Machine Learning Task

Step 3. Identify Key Evaluation Metrics

Step 4. Build and Test Machine Learning Models

## 1. Identify the Business Problem

<i><b>For Jan</b>: Rephrase motivation and main problem</i>

## 2. Identify the Machine Learning Task

What will the machine learning model do?
- Goal is to predict the class label (i.e. haplogroup) choice from a predefined list of states (i.e. 27 Y-STRs)

Classification Problem
- Input: Y-STRs (e.g Column DYS576, Column DYS627)
- Output: Haplogroups (i.e. Column haplogroup)

Since this is a classification problem, the following models will be utilized.
1. KNN
2. LDA
3. Gaussian Naive Bayes
4. Decision Tree
5. Random Forest
6. Gradient Boosting

For KNN, scaling will be applied during the data preprocessing to help with faster convergence, equal feature contribution, and improved performance [2][3].

Note that Logistic Regression (L1, L2) will not be used because of the assumption of linearity between the dependent variable and the independent variables [4]. Given that the dataset has overlapping classes as seen in 4.2 EDA, it will be difficult to establish the linearity between the target and the features.

SVM will also not be used because the dataset has overlapping classes [5]. As an example, plotting two of the features (i.e. DYS627 and DYS576) show overlaps between the four haplogroups (i.e. R1a1a1b2a2, O2a2b1a1a1, O2a2a1, O2a2b1a2a1) as seen in 4.2 EDA

## 3. Identify Key Evaluation Metrics

<i><b>For Jan</b>: What evaluation metric will we use? If we will use Accuracy, explain why we will use Accuracy as the evalutation metric.

We also need to look for any industry benchmarks on Accuracy. Otherwise, we can proceed to using PCC.</i>

Evaluation Metrics: Classification
- Accuracy: use when the goal is to minimize the overall error state
- Precision: use when the cost of false positives is high
- Recall: use when the cost of false negatives is high
- F1-score: use if you want to optimize precision and recall at the same time

### PCC for Benchmark

## 4. Build and Test Machine Learning Models

In [9]:
import numpy as np
import pandas as pd
import time
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import LinearSVC, SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import ShuffleSplit
from sklearn.ensemble import RandomForestClassifier

### 4.1 Data Preprocessing

In [10]:
# Step 1. Load dataset
df = pd.read_excel('Supplemental Processed Data Set.xlsx', sheet_name='S Table 1', skiprows=1)
df

haplogroup  number of haplotypes  \
0            C2b1a1a                   4.0   
1                NaN                   NaN   
2                NaN                   NaN   
3                NaN                   NaN   
4     O2a2b1a1a1a4a1                   6.0   
...              ...                   ...   
4059             NaN                   NaN   
4060             NaN                   NaN   
4061             NaN                   NaN   
4062             NaN                   NaN   
4063             NaN                   NaN   

                                              haplotype  total frequency  \
0     [19.0, 14.0, 22.0, 31.0, 22.0, 10.0, 17.0, 16....              1.0   
1     [19.0, 14.0, 22.0, 30.0, 22.0, 10.0, 18.0, 17....              1.0   
2     [18.0, 14.0, 21.0, 31.0, 24.0, 10.0, 17.0, 16....              1.0   
3     [19.0, 14.0, 22.0, 30.0, 20.0, 10.0, 18.0, 17....              1.0   
4     [18.0, 12.0, 20.0, 29.0, 19.0, 9.0, 18.0, 14.0...              1.0   
...                                                 ...              ...   
4059  [20.0, 12.0, 20.0, 28.0, 21.0, 10.0, 15.0, 15....              1.0   
4060  [18.0, 12.0, 21.0, 28.0, 21.0, 10.0, 17.0, 15....              1.0   
4061  [19.0, 12.0, 21.0, 28.0, 21.0, 10.0, 18.0, 16....              1.0   
4062  [16.0, 14.0, 21.0, 29.0, 22.0, 11.0, 16.0, 15....              1.0   
4063  [17.0, 12.0, 21.0, 28.0, 23.0, 10.0, 17.0, 16....              1.0   

          sampleID            population  frequency  
0           HLM100  Hulunbuir[Mongolian]        1.0  
1           HHM158     Hohhot[Mongolian]        1.0  
2           ODM030      Ordos[Mongolian]        1.0  
3           HLM178  Hulunbuir[Mongolian]        1.0  
4           HHM088     Hohhot[Mongolian]        1.0  
...            ...                   ...        ...  
4059  HaiN153(Han)                   Han        1.0  
4060    GD-16(Han)                   Han        1.0  
4061    JX-82(Han)                   Han        1.0  
4062  HaiN139(Han)                   Han        1.0  
4063    SX-92(Han)                   Han        1.0  

[4064 rows x 7 columns]

In [11]:
# Step 2. Fill NaN values
df = df.ffill()
df

haplogroup  number of haplotypes  \
0            C2b1a1a                   4.0   
1            C2b1a1a                   4.0   
2            C2b1a1a                   4.0   
3            C2b1a1a                   4.0   
4     O2a2b1a1a1a4a1                   6.0   
...              ...                   ...   
4059      O2a1c1a1a1                  14.0   
4060      O2a1c1a1a1                  14.0   
4061      O2a1c1a1a1                  14.0   
4062      O2a1c1a1a1                  14.0   
4063      O2a1c1a1a1                  14.0   

                                              haplotype  total frequency  \
0     [19.0, 14.0, 22.0, 31.0, 22.0, 10.0, 17.0, 16....              1.0   
1     [19.0, 14.0, 22.0, 30.0, 22.0, 10.0, 18.0, 17....              1.0   
2     [18.0, 14.0, 21.0, 31.0, 24.0, 10.0, 17.0, 16....              1.0   
3     [19.0, 14.0, 22.0, 30.0, 20.0, 10.0, 18.0, 17....              1.0   
4     [18.0, 12.0, 20.0, 29.0, 19.0, 9.0, 18.0, 14.0...              1.0   
...                                                 ...              ...   
4059  [20.0, 12.0, 20.0, 28.0, 21.0, 10.0, 15.0, 15....              1.0   
4060  [18.0, 12.0, 21.0, 28.0, 21.0, 10.0, 17.0, 15....              1.0   
4061  [19.0, 12.0, 21.0, 28.0, 21.0, 10.0, 18.0, 16....              1.0   
4062  [16.0, 14.0, 21.0, 29.0, 22.0, 11.0, 16.0, 15....              1.0   
4063  [17.0, 12.0, 21.0, 28.0, 23.0, 10.0, 17.0, 16....              1.0   

          sampleID            population  frequency  
0           HLM100  Hulunbuir[Mongolian]        1.0  
1           HHM158     Hohhot[Mongolian]        1.0  
2           ODM030      Ordos[Mongolian]        1.0  
3           HLM178  Hulunbuir[Mongolian]        1.0  
4           HHM088     Hohhot[Mongolian]        1.0  
...            ...                   ...        ...  
4059  HaiN153(Han)                   Han        1.0  
4060    GD-16(Han)                   Han        1.0  
4061    JX-82(Han)                   Han        1.0  
4062  HaiN139(Han)                   Han        1.0  
4063    SX-92(Han)                   Han        1.0  

[4064 rows x 7 columns]

In [12]:
# Step 3. Split haplotype into separate columns
df = pd.concat([df, df['haplotype'].str.replace('[', '').str.replace(']', '').str.split(',', expand=True)], axis=1)
YSTRs = {0: "DYS576", 1: "DYS389 I", 2: "DYS635", 3: "DYS389 II", 4: "DYS627", 5: "DYS460", 6: "DYS458",
                 7: "DYS19", 8: "Y-GATA-H4", 9: "DYS448", 10: "DYS391", 11: "DYS456", 12: "DYS390", 13: "DYS438", 
                 14: "DYS392", 15: "DYS518", 16: "DYS570", 17: "DYS437", 18: "DYS385a", 19: "DYS385b", 20: "DYS449", 
                 21: "DYS393", 22: "DYS439", 23: "DYS481", 24: "DYS576a", 25: "DYS576b", 26: "DYS533"
}

df = df.rename(columns=YSTRs)
df = df.drop(columns=['haplotype'])
df

haplogroup  number of haplotypes  total frequency      sampleID  \
0            C2b1a1a                   4.0              1.0        HLM100   
1            C2b1a1a                   4.0              1.0        HHM158   
2            C2b1a1a                   4.0              1.0        ODM030   
3            C2b1a1a                   4.0              1.0        HLM178   
4     O2a2b1a1a1a4a1                   6.0              1.0        HHM088   
...              ...                   ...              ...           ...   
4059      O2a1c1a1a1                  14.0              1.0  HaiN153(Han)   
4060      O2a1c1a1a1                  14.0              1.0    GD-16(Han)   
4061      O2a1c1a1a1                  14.0              1.0    JX-82(Han)   
4062      O2a1c1a1a1                  14.0              1.0  HaiN139(Han)   
4063      O2a1c1a1a1                  14.0              1.0    SX-92(Han)   

                population  frequency DYS576 DYS389 I DYS635 DYS389 II  ...  \
0     Hulunbuir[Mongolian]        1.0   19.0     14.0   22.0      31.0  ...   
1        Hohhot[Mongolian]        1.0   19.0     14.0   22.0      30.0  ...   
2         Ordos[Mongolian]        1.0   18.0     14.0   21.0      31.0  ...   
3     Hulunbuir[Mongolian]        1.0   19.0     14.0   22.0      30.0  ...   
4        Hohhot[Mongolian]        1.0   18.0     12.0   20.0      29.0  ...   
...                    ...        ...    ...      ...    ...       ...  ...   
4059                   Han        1.0   20.0     12.0   20.0      28.0  ...   
4060                   Han        1.0   18.0     12.0   21.0      28.0  ...   
4061                   Han        1.0   19.0     12.0   21.0      28.0  ...   
4062                   Han        1.0   16.0     14.0   21.0      29.0  ...   
4063                   Han        1.0   17.0     12.0   21.0      28.0  ...   

     DYS437 DYS385a DYS385b DYS449 DYS393 DYS439 DYS481 DYS576a DYS576b DYS533  
0      14.0    11.0    19.0   30.0   14.0   12.0   24.0    36.0    39.0   12.0  
1      14.0    11.0    17.0   30.0   14.0   14.0   24.0    39.0    39.0   12.0  
2      14.0    11.0    19.0   30.0   14.0   12.0   23.0    37.0    38.0   12.0  
3      14.0    11.0    17.0   30.0   14.0   14.0   24.0    39.0    39.0   12.0  
4      16.0    14.0    18.0   32.0   11.0   13.0   23.0    35.0    37.0   11.0  
...     ...     ...     ...    ...    ...    ...    ...     ...     ...    ...  
4059   14.0    13.0    13.0   31.0   13.0   11.0   25.0    37.0    40.0   11.0  
4060   14.0    12.0    19.0   31.0   12.0   12.0   28.0    36.0    38.0   11.0  
4061   14.0    12.0    19.0   33.0   12.0   12.0   26.0    36.0    39.0   11.0  
4062   14.0    12.0    18.0   29.0   14.0   12.0   23.0    37.0    39.0   11.0  
4063   14.0    12.0    19.0   31.0   12.0   11.0   27.0    36.0    38.0   11.0  

[4064 rows x 33 columns]

### Random Forest

In [19]:
n_splits = 20         # number of random train/test splits (trials)
test_size = 0.25      # proportion for test set
# max_depth_settings = range(1, 21)
max_depth_settings = range(25, 28, 1)
# n_estimators_settings = [10, 50, 100, 200]
n_estimators_settings = range(350, 501, 50) #, 401, 200)

def train_random_forest_mc(X, y):
    start_time = time.time()
    results = []

    # MCCV
    cv = ShuffleSplit(n_splits=n_splits, test_size=test_size, random_state=42)

    for n_est in n_estimators_settings:
        for depth in max_depth_settings:
            split_scores = []

            for train_idx, test_idx in cv.split(X, y):
                X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
                y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]

                clf = RandomForestClassifier(
                    n_estimators=n_est,
                    max_depth=depth,
                    random_state=42,
                    n_jobs=-1,
                    min_samples_leaf=1,
                    max_features=0.3,
                    class_weight="balanced"
                )
                clf.fit(X_train, y_train)
                split_scores.append(clf.score(X_test, y_test))

            results.append({
                "n_estimators": n_est,
                "max_depth": depth,
                "mean_acc": np.mean(split_scores)
            })

    df_results = pd.DataFrame(results)
    best_row = df_results.loc[df_results["mean_acc"].idxmax()]
    best_score = best_row["mean_acc"]
    best_depth = int(best_row["max_depth"])
    best_nest = int(best_row["n_estimators"])

    final_model = RandomForestClassifier(
        n_estimators=best_nest,
        max_depth=best_depth,
        random_state=42,
        n_jobs=-1
    )
    final_model.fit(X, y)

    importances = pd.Series(final_model.feature_importances_, index=X.columns)
    top_predictor = importances.idxmax()

    run_time = time.time() - start_time

    return [
        'Random Forest',
        best_score,
        f'n_estimators = {best_nest}, max_depth = {best_depth}',
        top_predictor,
        run_time
    ]

In [15]:
# -----------------------------------------------------------
#  MUTATION-AWARE FEATURE ENGINEERING FOR YFILER PLUS (27 loci)
# -----------------------------------------------------------

# Identify key columns
haplogroup_col = df.columns[0]
str_cols = df.columns[6:]   # STR integer allele columns
# Force numeric conversion (safe and required)
df[str_cols] = df[str_cols].apply(pd.to_numeric, errors="coerce")
# -----------------------------------------------------------
# YFILER PLUS MUTATION RATE GROUPS (categorical only)
# -----------------------------------------------------------

fast_loci = [
    "DYS570", "DYS576", "DYS458", "DYS449", "DYS627", "DYS481"
]

intermediate_loci = [
    "DYS385a", "DYS385b", "DYS533", "DYS19", "DYS391", "DYS518",
    "DYS635", "DYS390", "DYS392", "DYS393"
]

slow_loci = [
    "DYS438", "DYS437", "DYS439", "DYS389I", "DYS389II",
    "DYS460", "DYS456", "Y_GATA_H4", "DYS448"
]

# Some datasets name DYS385 as a single column; handle safely
fast_loci = [col for col in fast_loci if col in str_cols]
intermediate_loci = [col for col in intermediate_loci if col in str_cols]
slow_loci = [col for col in slow_loci if col in str_cols]

# -----------------------------------------------------------
# 1. HAPLOGROUP CENTROIDS
# -----------------------------------------------------------
centroids = df.groupby(haplogroup_col)[str_cols].mean()

def compute_l1_distance(row):
    centroid = centroids.loc[row[haplogroup_col]]
    return np.abs(row[str_cols] - centroid).sum()

df["l1_dist_to_centroid"] = df.apply(compute_l1_distance, axis=1)

# -----------------------------------------------------------
# 2. MUTATION-WEIGHTED DISTANCE TO CENTROID
#    (fast loci count more, slow loci count less)
# -----------------------------------------------------------
# Assign categorical weights
weights = {}
for col in fast_loci:
    weights[col] = 3.0
for col in intermediate_loci:
    weights[col] = 2.0
for col in slow_loci:
    weights[col] = 1.0

# Default any remaining loci to medium weight
for col in str_cols:
    if col not in weights:
        weights[col] = 2.0

def compute_weighted_l1(row):
    centroid = centroids.loc[row[haplogroup_col]]
    diffs = (row[str_cols] - centroid).abs()
    weighted = [diffs[c] * weights[c] for c in str_cols]
    return np.sum(weighted)

df["weighted_l1_centroid"] = df.apply(compute_weighted_l1, axis=1)

# -----------------------------------------------------------
# 3. PER-LOCUS CENTERING (global mean normalization)
# -----------------------------------------------------------
global_means = df[str_cols].mean()
centered_df = df[str_cols] - global_means
centered_df = centered_df.add_suffix("_centered")
df = pd.concat([df, centered_df], axis=1)

# -----------------------------------------------------------
# 4. GLOBAL SUMMARY FEATURES
# -----------------------------------------------------------
df["allele_sum"] = df[str_cols].sum(axis=1)
df["allele_variance"] = df[str_cols].var(axis=1)
df["num_fast_above_mean"] = (df[fast_loci] > global_means[fast_loci]).sum(axis=1)
df["num_slow_above_mean"] = (df[slow_loci] > global_means[slow_loci]).sum(axis=1)

# -----------------------------------------------------------
# 5. FAST-LOCUS VARIABILITY INDEX
# -----------------------------------------------------------
df["fast_variance"] = df[fast_loci].var(axis=1)

# -----------------------------------------------------------
# 6. SLOW-LOCUS STABILITY SCORE
#    (small deviations from mean → more stable)
# -----------------------------------------------------------
df["slow_stability"] = -df[slow_loci].sub(global_means[slow_loci], axis=1).abs().sum(axis=1)

# -----------------------------------------------------------
# 7. PAIRWISE ABSOLUTE DIFFERENCES (full STR geometry)
# -----------------------------------------------------------
pairwise_features = {}
cols = list(str_cols)

for i in range(len(cols)):
    for j in range(i+1, len(cols)):
        name = f"absdiff_{cols[i]}_{cols[j]}"
        pairwise_features[name] = (df[cols[i]] - df[cols[j]]).abs()

pairwise_df = pd.DataFrame(pairwise_features)
df = pd.concat([df, pairwise_df], axis=1)

print("✅ Mutation-aware feature engineering complete!")
print(f"Total features: {df.shape[1]}")

✅ Mutation-aware feature engineering complete!
Total features: 419


In [20]:
X = df.iloc[:, 6:]
y = df.iloc[:, 0]

random_forest_df = train_random_forest_mc(X, y)
print(random_forest_df)

['Random Forest', 0.6398129921259842, 'n_estimators = 450, max_depth = 27', 'l1_dist_to_centroid', 1663.6826756000519]


In [18]:
from sklearn.model_selection import RandomizedSearchCV, ShuffleSplit
# Cross-validation setup
cv = ShuffleSplit(n_splits=20, test_size=0.25, random_state=42)

param_dist = {
    "n_estimators": np.arange(200, 601, 50),   # 200–600 trees
    "max_depth": [5, 8, 15, 18, 25, 27],       # cleaned list
    "min_samples_leaf": [1, 2],               # small leaf sizes give smoother trees
    "max_features": ["sqrt", 0.3, 0.5],       # allow some variation
    "criterion": ["gini"]                     # for Y-STR, gini is best
}

rf = RandomForestClassifier(random_state=42, n_jobs=-1)

# RandomizedSearchCV for RF
rs = RandomizedSearchCV(
    estimator=rf,
    param_distributions=param_dist,
    n_iter=60,                  # # of random configurations tested
    scoring="accuracy",
    cv=cv,
    verbose=2,
    random_state=42,
    n_jobs=-1
)

# Run the search
rs.fit(X, y)

print("Best score:", rs.best_score_)
print("Best params:", rs.best_params_)

# Best RF model
best_rf = rs.best_estimator_

Fitting 20 folds for each of 60 candidates, totalling 1200 fits
Best score: 0.6862696850393701
Best params: {'n_estimators': 350, 'min_samples_leaf': 1, 'max_features': 'sqrt', 'max_depth': 25, 'criterion': 'gini'}


### Gradient Boosting

In [4]:
# Step 1. Load dataset
df = pd.read_excel('Supplemental Processed Data Set.xlsx', sheet_name='S Table 1', skiprows=1)
# Step 2. Fill NaN values
df = df.ffill()
# Step 3. Split haplotype into separate columns
df = pd.concat([df, df['haplotype'].str.replace('[', '').str.replace(']', '').str.split(',', expand=True)], axis=1)
YSTRs = {0: "DYS576", 1: "DYS389 I", 2: "DYS635", 3: "DYS389 II", 4: "DYS627", 5: "DYS460", 6: "DYS458",
                 7: "DYS19", 8: "Y-GATA-H4", 9: "DYS448", 10: "DYS391", 11: "DYS456", 12: "DYS390", 13: "DYS438", 
                 14: "DYS392", 15: "DYS518", 16: "DYS570", 17: "DYS437", 18: "DYS385a", 19: "DYS385b", 20: "DYS449", 
                 21: "DYS393", 22: "DYS439", 23: "DYS481", 24: "DYS576a", 25: "DYS576b", 26: "DYS533"
}

df = df.rename(columns=YSTRs)
df = df.drop(columns=['haplotype'])
df

haplogroup  number of haplotypes  total frequency      sampleID  \
0            C2b1a1a                   4.0              1.0        HLM100   
1            C2b1a1a                   4.0              1.0        HHM158   
2            C2b1a1a                   4.0              1.0        ODM030   
3            C2b1a1a                   4.0              1.0        HLM178   
4     O2a2b1a1a1a4a1                   6.0              1.0        HHM088   
...              ...                   ...              ...           ...   
4059      O2a1c1a1a1                  14.0              1.0  HaiN153(Han)   
4060      O2a1c1a1a1                  14.0              1.0    GD-16(Han)   
4061      O2a1c1a1a1                  14.0              1.0    JX-82(Han)   
4062      O2a1c1a1a1                  14.0              1.0  HaiN139(Han)   
4063      O2a1c1a1a1                  14.0              1.0    SX-92(Han)   

                population  frequency DYS576 DYS389 I DYS635 DYS389 II  ...  \
0     Hulunbuir[Mongolian]        1.0   19.0     14.0   22.0      31.0  ...   
1        Hohhot[Mongolian]        1.0   19.0     14.0   22.0      30.0  ...   
2         Ordos[Mongolian]        1.0   18.0     14.0   21.0      31.0  ...   
3     Hulunbuir[Mongolian]        1.0   19.0     14.0   22.0      30.0  ...   
4        Hohhot[Mongolian]        1.0   18.0     12.0   20.0      29.0  ...   
...                    ...        ...    ...      ...    ...       ...  ...   
4059                   Han        1.0   20.0     12.0   20.0      28.0  ...   
4060                   Han        1.0   18.0     12.0   21.0      28.0  ...   
4061                   Han        1.0   19.0     12.0   21.0      28.0  ...   
4062                   Han        1.0   16.0     14.0   21.0      29.0  ...   
4063                   Han        1.0   17.0     12.0   21.0      28.0  ...   

     DYS437 DYS385a DYS385b DYS449 DYS393 DYS439 DYS481 DYS576a DYS576b DYS533  
0      14.0    11.0    19.0   30.0   14.0   12.0   24.0    36.0    39.0   12.0  
1      14.0    11.0    17.0   30.0   14.0   14.0   24.0    39.0    39.0   12.0  
2      14.0    11.0    19.0   30.0   14.0   12.0   23.0    37.0    38.0   12.0  
3      14.0    11.0    17.0   30.0   14.0   14.0   24.0    39.0    39.0   12.0  
4      16.0    14.0    18.0   32.0   11.0   13.0   23.0    35.0    37.0   11.0  
...     ...     ...     ...    ...    ...    ...    ...     ...     ...    ...  
4059   14.0    13.0    13.0   31.0   13.0   11.0   25.0    37.0    40.0   11.0  
4060   14.0    12.0    19.0   31.0   12.0   12.0   28.0    36.0    38.0   11.0  
4061   14.0    12.0    19.0   33.0   12.0   12.0   26.0    36.0    39.0   11.0  
4062   14.0    12.0    18.0   29.0   14.0   12.0   23.0    37.0    39.0   11.0  
4063   14.0    12.0    19.0   31.0   12.0   11.0   27.0    36.0    38.0   11.0  

[4064 rows x 33 columns]

In [ ]:
# ======================================================
# 3️⃣ MUTATION-AWARE FEATURE ENGINEERING (Robust Version)
# ======================================================

# ------------------------------------------------------
# Define Yfiler Plus mutation-rate groups (canonical names)
# ------------------------------------------------------
fast_loci = ["DYS570","DYS576","DYS458","DYS449","DYS627","DYS481"]
intermediate_loci = ["DYS385a","DYS385b","DYS533","DYS19","DYS391","DYS518","DYS635","DYS390","DYS392","DYS393"]
slow_loci = ["DYS438","DYS437","DYS439","DYS389I","DYS389II","DYS460","DYS456","Y_GATA_H4","DYS448"]

# ------------------------------------------------------
# Identify available STR columns in your dataframe
# ------------------------------------------------------
available_str_cols = [c for c in df.columns if any(k in c for k in ["DYS","Y_GATA","YGATA"])]
print(f"Detected {len(available_str_cols)} STR columns:", available_str_cols)

# ------------------------------------------------------
# Adjust loci lists to only include those present
# ------------------------------------------------------
fast_loci = [l for l in fast_loci if l in df.columns]
intermediate_loci = [l for l in intermediate_loci if l in df.columns]
slow_loci = [l for l in slow_loci if l in df.columns]
str_cols = list(set(fast_loci + intermediate_loci + slow_loci))

print(f"\nUsing {len(str_cols)} STR loci after filtering:")
print(str_cols)

# ------------------------------------------------------
# Ensure numeric STR data
# ------------------------------------------------------
df[str_cols] = df[str_cols].apply(pd.to_numeric, errors='coerce')

# ------------------------------------------------------
# Compute haplogroup centroids
# ------------------------------------------------------
hap_col = df.columns[0]
centroids = df.groupby(hap_col)[str_cols].mean()

# ------------------------------------------------------
# L1 distance to haplogroup centroid
# ------------------------------------------------------
def l1_to_centroid(row):
    hg = row[hap_col]
    if hg not in centroids.index:
        return np.nan
    centroid = centroids.loc[hg]
    return np.abs(row[str_cols] - centroid).sum()

df["l1_centroid"] = df.apply(l1_to_centroid, axis=1)

# ------------------------------------------------------
# Weighted L1 (fast=3, intermediate=2, slow=1)
# ------------------------------------------------------
weights = {l:3 for l in fast_loci}
weights.update({l:2 for l in intermediate_loci})
weights.update({l:1 for l in slow_loci})

df["weighted_l1_centroid"] = df.apply(
    lambda r: sum(abs(r[c] - centroids.loc[r[hap_col], c]) * weights.get(c, 2)
                  for c in str_cols if c in centroids.columns),
    axis=1
)

# ------------------------------------------------------
# Global allele statistics
# ------------------------------------------------------
df["allele_sum"] = df[str_cols].sum(axis=1)
df["allele_var"] = df[str_cols].var(axis=1)
if fast_loci:
    df["fast_var"] = df[fast_loci].var(axis=1)
else:
    df["fast_var"] = np.nan
if slow_loci:
    df["slow_stability"] = -df[slow_loci].sub(df[slow_loci].mean(), axis=1).abs().sum(axis=1)
else:
    df["slow_stability"] = np.nan

print("\n✅ Mutation-aware features added successfully:")
print(["l1_centroid", "weighted_l1_centroid", "allele_sum", "allele_var", "fast_var", "slow_stability"])


KeyError: "['DYS389I', 'DYS389II', 'Y_GATA_H4'] not in index"

In [ ]:
# ===============================================
# LightGBM + Custom Split (keeps singletons) + SMOTE
# ===============================================

import numpy as np
import pandas as pd
from lightgbm import LGBMClassifier
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.metrics import classification_report, balanced_accuracy_score, f1_score
from imblearn.over_sampling import SMOTE

# -----------------------------
# 1) Prepare X (numeric only) and y (labels)
# -----------------------------
y = df.iloc[:, 0]                   # haplogroup labels
X = df.iloc[:, 6:]                  # STR + engineered features
X = X.apply(pd.to_numeric, errors='coerce')  # ensure numeric (LightGBM handles NaN)

# -----------------------------
# 2) Custom split:
#    - Stratified split on classes with >= 2 samples
#    - Put singleton classes entirely in TRAIN
# -----------------------------
# mask == True for rows whose class appears >= 2 times
mask = y.value_counts()[y].values > 1
X_filtered, y_filtered = X[mask], y[mask]

sss = StratifiedShuffleSplit(n_splits=1, test_size=0.25, random_state=42)
for train_idx, test_idx in sss.split(X_filtered, y_filtered):
    X_train, X_test = X_filtered.iloc[train_idx], X_filtered.iloc[test_idx]
    y_train, y_test = y_filtered.iloc[train_idx], y_filtered.iloc[test_idx]

# add all singleton classes to TRAIN
X_train = pd.concat([X_train, X[~mask]], axis=0)
y_train = pd.concat([y_train, y[~mask]], axis=0)

print(f"Train size: {X_train.shape[0]} | Test size: {X_test.shape[0]}")
print(f"Unique classes — train: {y_train.nunique()} | test: {y_test.nunique()} | total: {y.nunique()}")

# -----------------------------
# 3) SMOTE on the TRAIN set only (k_neighbors=1 for ultra-rare classes)
# -----------------------------
smote = SMOTE(k_neighbors=1, random_state=42)
X_res, y_res = smote.fit_resample(X_train, y_train)
print(f"After SMOTE — train size: {X_res.shape[0]} | classes: {pd.Series(y_res).nunique()}")

# -----------------------------
# 4) Train LightGBM with imbalance handling
# -----------------------------
lgbm = LGBMClassifier(
    n_estimators=600,
    learning_rate=0.05,
    num_leaves=31,
    max_depth=-1,
    is_unbalance=True,   # additional imbalance handling
    n_jobs=-1,
    random_state=42
)

lgbm.fit(X_res, y_res)

# -----------------------------
# 5) Evaluate
# -----------------------------
y_pred = lgbm.predict(X_test)
bal_acc = balanced_accuracy_score(y_test, y_pred)
macro_f1 = f1_score(y_test, y_pred, average='macro')

print(f"\n✅ Balanced Accuracy: {bal_acc:.4f}")
print(f"✅ Macro F1:         {macro_f1:.4f}\n")
print("Classification report:\n")
print(classification_report(y_test, y_pred, digits=3))


NameError: name 'df' is not defined

In [ ]:
# ======================================================
# FIXED: Hierarchical LightGBM Classifier (Handles Singletons + Safe Splits)
# ======================================================

import re
import numpy as np
import pandas as pd
from collections import defaultdict
from lightgbm import LGBMClassifier
from sklearn.metrics import classification_report
from sklearn.model_selection import StratifiedShuffleSplit, train_test_split

# ---------------------------------------------
# 1️⃣ Extract major clade (e.g. 'O', 'C', 'N', 'R', etc.)
# ---------------------------------------------
df['major_clade'] = df.iloc[:, 0].str.extract(r'^([A-Z])')

# ---------------------------------------------
# 2️⃣ Prepare numeric features (LightGBM-safe)
# ---------------------------------------------
X = df.iloc[:, 6:].apply(pd.to_numeric, errors='coerce')  # STR + engineered features
y_major = df['major_clade']                              # top-level label
y_full = df.iloc[:, 0]                                   # full haplogroup label

# ---------------------------------------------
# 3️⃣ Custom split for major clade classifier
#     - keeps singletons in training
# ---------------------------------------------
mask = y_major.value_counts()[y_major].values > 1
X_filtered = X[mask]
y_filtered = y_major[mask]

sss = StratifiedShuffleSplit(n_splits=1, test_size=0.25, random_state=42)
for train_idx, test_idx in sss.split(X_filtered, y_filtered):
    X_train, X_test = X_filtered.iloc[train_idx], X_filtered.iloc[test_idx]
    y_train, y_test = y_filtered.iloc[train_idx], y_filtered.iloc[test_idx]

# Add singletons (major clades with 1 sample) entirely to training set
X_train = pd.concat([X_train, X[~mask]])
y_train = pd.concat([y_train, y_major[~mask]])

print(f"✅ Train size: {len(X_train)} | Test size: {len(X_test)}")
print(f"✅ Unique major clades — train: {y_train.nunique()}, test: {y_test.nunique()}")

# ---------------------------------------------
# 4️⃣ Train major clade classifier
# ---------------------------------------------
clf_major = LGBMClassifier(
    n_estimators=400,
    learning_rate=0.05,
    num_leaves=31,
    is_unbalance=True,
    n_jobs=-1,
    random_state=42
)
clf_major.fit(X_train, y_train)
y_major_pred = clf_major.predict(X_test)

print("\n✅ Major Haplogroup (Top-Level) Report:\n")
print(classification_report(y_test, y_major_pred, digits=3))

# ---------------------------------------------
# 5️⃣ Train subclade classifiers per major clade
# ---------------------------------------------
sub_models = {}
print("\n🔹 Training subclade classifiers...\n")

for clade in df['major_clade'].unique():
    sub_df = df[df['major_clade'] == clade]
    sub_X = sub_df.iloc[:, 6:].apply(pd.to_numeric, errors='coerce')
    sub_y = sub_df.iloc[:, 0]  # full haplogroup name

    # Skip clades with too few samples
    if sub_y.nunique() < 3 or len(sub_y) < 10:
        print(f"⚠️ Skipping {clade}: only {len(sub_y)} samples, {sub_y.nunique()} unique subclades.")
        continue

    # Safe split: if some subclades have only 1 sample, avoid stratify
    try:
        Xs_train, Xs_test, ys_train, ys_test = train_test_split(
            sub_X, sub_y, test_size=0.25, stratify=sub_y, random_state=42
        )
    except ValueError:
        Xs_train, Xs_test, ys_train, ys_test = train_test_split(
            sub_X, sub_y, test_size=0.25, random_state=42
        )

    model = LGBMClassifier(
        n_estimators=400,
        learning_rate=0.05,
        num_leaves=31,
        is_unbalance=True,
        n_jobs=-1,
        random_state=42
    )
    model.fit(Xs_train, ys_train)
    sub_models[clade] = model

    y_sub_pred = model.predict(Xs_test)
    print(f"\n✅ Subclade model for {clade}: trained on {len(ys_train)} samples, {sub_y.nunique()} subclades.")
    print(classification_report(ys_test, y_sub_pred, digits=3))

print("\n✅ All hierarchical models trained successfully!")

✅ Train size: 3048 | Test size: 1016
✅ Unique major clades — train: 13, test: 13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000173 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 296
[LightGBM] [Info] Number of data points in the train set: 3048, number of used features: 27
[LightGBM] [Info] Start training from score -1.993962
[LightGBM] [Info] Start training from score -2.699231
[LightGBM] [Info] Start training from score -5.077802
[LightGBM] [Info] Start training from score -5.383184
[LightGBM] [Info] Start training from score -5.457292
[LightGBM] [Info] Start training from score -5.825016
[LightGBM] [Info] Start training from score -3.652793
[LightGBM] [Info] Start training from score -5.383184
[LightGBM] [Info] Start training from score -2.704121
[L

c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

Exception ignored on calling ctypes callback function: <function _log_callback at 0x000001E15B053C40>
Traceback (most recent call last):
  File "C:\Users\Admin\AppData\Roaming\Python\Python312\site-packages\lightgbm\basic.py", line 287, in _log_callback
    def _log_callback(msg: bytes) -> None:
    
KeyboardInterrupt: 


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

...

c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packag

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


              precision    recall  f1-score   support

          N1      0.333     0.500     0.400         4
         N1a      1.000     0.250     0.400         4
       N1a1a      0.750     0.600     0.667         5
  N1a1a1a1a3      0.500     1.000     0.667         1
 N1a1a1a1a3a      1.000     1.000     1.000        10
  N1a1a1a1a4      1.000     1.000     1.000         2
        N1a2      0.917     1.000     0.957        11
         N1b      0.636     0.875     0.737        16
    N1b1a1b~      0.000     0.000     0.000         1
        N1b2      0.000     0.000     0.000         2
    N1b2a1b~      1.000     0.750     0.857        12

    accuracy                          0.779        68
   macro avg      0.649     0.634     0.608        68
weighted avg      0.792     0.779     0.762        68

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000082 seconds.
You

c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


# Results

In [39]:
automl_df = pd.DataFrame(columns=['Machine Learning Method', 'Test Accuracy', 'Best Parameter', 'Top Predictor Variable', 'Run Time'])

automl_df.loc[0] = knn_df
automl_df.loc[1] = lda_df
automl_df.loc[2] = gnb_df
automl_df.loc[3] = dt_df
automl_df.loc[4] = random_forest_df
# automl_df.loc[5] = gbm_df

automl_df = automl_df.drop(columns='Top Predictor Variable')
automl_df

Machine Learning Method  Test Accuracy  \
0                     kNN       0.607726   
1                     LDA       0.583415   
2             Gaussian NB       0.421604   
3           Decision Tree       0.517028   
4           Random Forest       0.681152   

                                      Best Parameter    Run Time  
0                                     N_Neighbor = 1  577.361708  
1                                       solver = svd    5.384096  
2                              var_smoothing = 1e-06   10.045185  
3  criterion = entropy, max_depth = None, min_sam...   48.732992  
4                 n_estimators = 200, max_depth = 16  523.571158

<b>Discussion</b>

Consider doing a confusion matrix?? For random forest, check where mistakes/confusions were made

Note:
- kNN is more suited for data with non-linear relationships
- Logistic Regression is more suited for binary classification problems, and assumes linearity between the dependent variable and independent variables
- SVM is more suited for datasets with no overlapping classes
- LDA is more suited for multi-class data classifications since it projects data into one dimension for easier classification (i.e. dimensionality reduction)
- Gaussian Naive Bayes is more suited for continuous data as it assumes the values follow a normal distribution
- Decision Tree and Random Forest are more suited for rule based problems, and handling discrete data
- GBM is prone to overfitting

# Recommendations

# References

[1] https://www.sciencedirect.com/science/article/abs/pii/S0379073824001944

[2] https://towardsdatascience.com/all-about-feature-scaling-bcc0ad75cb35/#:~:text=IN%20DEPTH%20ANALYSIS,scaling%20in%20the%20X%2DY%20plane.

[3] https://www.geeksforgeeks.org/machine-learning/Feature-Engineering-Scaling-Normalization-and-Standardization/

[4] https://www.geeksforgeeks.org/data-science/advantages-and-disadvantages-of-logistic-regression/

[5] https://medium.com/@haj122/when-and-when-not-to-use-svms-e9edea04d6ba